### 필요한 모듈 임포트

In [3]:
from sentence_transformers import SentenceTransformer
from chromadb import PersistentClient
from fuzzywuzzy import fuzz
from web_crawler import MyWebCrawler
import pandas as pd
import numpy as np
import re
import emoji
import math

/Users/kimss/Documents/chromadb_merge/.conda/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


### Chroma DB 및 컬렉션(리뷰, 메뉴) 객체 정의

In [4]:
chroma_client = PersistentClient('/Users/kimss/Documents/test_chroma/merged_chroma_db')
review_collection = chroma_client.get_collection(name="review_collection")
menu_collection = chroma_client.get_collection(name="menu_collection")

### 컬렉션 정상 로드 여부 확인

In [3]:
review_collection

Collection(name=review_collection)

In [39]:
menu_collection

Collection(name=menu_collection)

### '링크' 메타데이터 업로드 (리뷰 컬렉션 기준)

In [5]:
results = review_collection.get(include=["metadatas"])

urls = []
for meta in results["metadatas"]:
  if meta and "링크" in meta:
    urls.append(meta["링크"])

### URL 정상 로드 여부 확인

In [6]:
print(urls)

['https://place.map.kakao.com/18214074', 'https://place.map.kakao.com/27076123', 'https://place.map.kakao.com/1165457187', 'https://place.map.kakao.com/21657018', 'https://place.map.kakao.com/882531039', 'https://place.map.kakao.com/1937596748', 'https://place.map.kakao.com/1092867118', 'https://place.map.kakao.com/27528617', 'https://place.map.kakao.com/1841364911', 'https://place.map.kakao.com/935677225', 'https://place.map.kakao.com/18691204', 'https://place.map.kakao.com/677270205', 'https://place.map.kakao.com/1419078831', 'https://place.map.kakao.com/1303358665', 'https://place.map.kakao.com/959512331', 'https://place.map.kakao.com/17127061', 'https://place.map.kakao.com/1366999935', 'https://place.map.kakao.com/958070379', 'https://place.map.kakao.com/1610234898', 'https://place.map.kakao.com/1276139149', 'https://place.map.kakao.com/1539239706', 'https://place.map.kakao.com/855108683', 'https://place.map.kakao.com/1298533381', 'https://place.map.kakao.com/339667159', 'https://p

### 웹 크롤링 시작

- **정상적으로 작동 안되는 경우 다음 명령어를 터미널에 입력**
- **그래도 안되면 컴퓨터 다시 시작 🥲**
- **주의: Chrome 사이트 강제 종료할 수 있음!!! 중요한 건 백업, 저장 필수**
```
pkill -f chromedriver
pkill -f Google\ Chrome
```

In [7]:
reviews = []

for url in urls:
  crawler = MyWebCrawler(url)
  crawler.collect_place_info()
  crawler.collect_reviews()
  crawler.quit_driver()
  
  crawler.info['url'] = url
  print(crawler.info)
  reviews.append(crawler.info)

{'상호명': '장소명알레그리아 판교테크노밸리점', '주소': '경기 성남시 분당구 판교역로 230 삼환하이펙스 B동 1층 119호 (우)13493', '역 정보': '판교역 1번 출구에서 675m', '도보 거리': '도보 14분', '전화번호': '031-696-0305', '요일별_영업시간': {'목': '08:00 ~ 20:30', '금': '08:00 ~ 20:30', '토': '10:00 ~ 20:30', '일': '10:00 ~ 20:30', '월': '08:00 ~ 20:30', '화': '08:00 ~ 20:30', '수': '08:00 ~ 20:30', '휴무일': '추석전날, 추석당일, 설전날, 설당일'}, '리뷰': {'리뷰 1': {'별점': 4, '리뷰 내용': '원두블렌딩을 원가절감한게 너무 과함. 종전 리뷰 후 다시 갔는데 프차긴 해도 가격,공간이 좋은편도 아니고 맛 하나 보고 가는 곳인데... 더보기', '날짜': '2025.06.24.'}, '리뷰 2': {'별점': 4, '리뷰 내용': '분위기 맛 친절 어느 하나 빼놓을 수 없는 맛집 ✨\n사람들로 항상 북적이는 곳', '날짜': '2025.04.14.'}, '리뷰 3': {'별점': 5, '리뷰 내용': '테크원점보다 여기가 더 맛있게 느껴짐. 라떼 맛있음. 근처 갈 일 있으면 종종 들리는 곳. 아이스크림 올라간 라떼도 꽤 별미.', '날짜': '2025.02.06.'}, '리뷰 4': {'별점': 5, '리뷰 내용': '라노체 우유거품 아인슈페너? 달달\n\n카카오라떼 코코... 더보기', '날짜': '2025.01.10.'}, '리뷰 5': {'별점': 3, '리뷰 내용': '리뷰 없음', '날짜': '2025.01.03.'}, '리뷰 6': {'별점': 5, '리뷰 내용': '리뷰 없음', '날짜': '2024.10.19.'}, '리뷰 7': {'별점': 3, '리뷰 내용': '리뷰 없음', '날짜': '2024.10.15.'}, '리뷰 8': {'별점': 3, '리뷰

### 리뷰 데이터프레임 생성

In [8]:
df_reviews = pd.DataFrame(reviews)

In [9]:
# 상호명 전처리
df_reviews['상호명'] = df_reviews['상호명'].str.replace(r'^장소명', '', regex=True)

In [10]:
df_reviews.head()

상호명                                                 주소  \
0    알레그리아 판교테크노밸리점     경기 성남시 분당구 판교역로 230 삼환하이펙스 B동 1층 119호 (우)13493   
1        스타벅스 판교역로점      경기 성남시 분당구 판교역로192번길 14 리치투게더센터 1-2층 (우)13524   
2     이디야커피 판교봇들마을점             경기 성남시 분당구 판교로 375 메가스페이스1 1층 (우)13489   
3       세시셀라 아브뉴프랑점                경기 성남시 분당구 동판교로177번길 25 1층 (우)13525   
4  메이크어케이크 아브뉴프랑판교점  경기 성남시 분당구 동판교로177번길 25 판교 호반 써밋 플레이스 1층 151호 ...   

               역 정보          도보 거리               전화번호  \
0  판교역 1번 출구에서 675m         도보 14분       031-696-0305   
1  판교역 1번 출구에서 225m          도보 5분          1522-3232   
2          23:00 까지  08:00 ~ 23:00       031-701-3337   
3  판교역 1번 출구에서 250m          도보 7분  매일  11:30 ~ 22:00   
4  판교역 1번 출구에서 319m          도보 8분       031-708-7040   

                                            요일별_영업시간  \
0  {'목': '08:00 ~ 20:30', '금': '08:00 ~ 20:30', '...   
1  {'목': '07:00 ~ 22:00', '금': '07:00 ~ 22:00', '...   
2  {'목': '08:00 ~ 23:00', '금': '08:00 ~ 23:00', '...   
3  {'월': '11:30 ~ 22:00', '화': '11:30 ~ 22:00', '...   
4  {'월': '12:00 ~ 21:50', '화': '12:00 ~ 21:50', '...   

                                                  리뷰  \
0  {'리뷰 1': {'별점': 4, '리뷰 내용': '원두블렌딩을 원가절감한게 너무 ...   
1  {'리뷰 1': {'별점': 5, '리뷰 내용': '넘 친절한 직원분들! 점심에는 ...   
2  {'리뷰 1': {'별점': 1, '리뷰 내용': '콜라보 굿즈 판매 안하는 매장입...   
3  {'리뷰 1': {'별점': 5, '리뷰 내용': '당근케익 추천받아가지고 포장해서...   
4  {'리뷰 1': {'별점': 3, '리뷰 내용': '리뷰 없음', '날짜': '20...   

                                      url  
0    https://place.map.kakao.com/18214074  
1    https://place.map.kakao.com/27076123  
2  https://place.map.kakao.com/1165457187  
3    https://place.map.kakao.com/21657018  
4   https://place.map.kakao.com/882531039

### 평균 별점 업데이트

In [11]:
def extract_avg_rating(review_data):
    if isinstance(review_data, dict):
        ratings = [r.get('별점', 0) for r in review_data.values() if isinstance(r, dict) and '별점' in r]
        return round(sum(ratings) / len(ratings), 2) if ratings else None
    return None

df_reviews['평균별점'] = df_reviews['리뷰'].apply(extract_avg_rating)

#### 위 코드로 파싱이 안되는 경우 아래 코드 진행(주석 해제 필요)

In [ ]:
# import ast
# 리뷰 컬럼을 딕셔너리로 파싱하고 평균 별점 계산
# def extract_avg_rating(review_str):
#     try:
#         reviews = ast.literal_eval(review_str)
#         ratings = [r['별점'] for r in reviews.values() if '별점' in r]
#         return round(sum(ratings) / len(ratings), 2) if ratings else None
#     except Exception:
#         return None

# df_reviews['평균별점'] = df_reviews['리뷰'].apply(extract_avg_rating)

In [12]:
df_reviews.head()

상호명                                                 주소  \
0    알레그리아 판교테크노밸리점     경기 성남시 분당구 판교역로 230 삼환하이펙스 B동 1층 119호 (우)13493   
1        스타벅스 판교역로점      경기 성남시 분당구 판교역로192번길 14 리치투게더센터 1-2층 (우)13524   
2     이디야커피 판교봇들마을점             경기 성남시 분당구 판교로 375 메가스페이스1 1층 (우)13489   
3       세시셀라 아브뉴프랑점                경기 성남시 분당구 동판교로177번길 25 1층 (우)13525   
4  메이크어케이크 아브뉴프랑판교점  경기 성남시 분당구 동판교로177번길 25 판교 호반 써밋 플레이스 1층 151호 ...   

               역 정보          도보 거리               전화번호  \
0  판교역 1번 출구에서 675m         도보 14분       031-696-0305   
1  판교역 1번 출구에서 225m          도보 5분          1522-3232   
2          23:00 까지  08:00 ~ 23:00       031-701-3337   
3  판교역 1번 출구에서 250m          도보 7분  매일  11:30 ~ 22:00   
4  판교역 1번 출구에서 319m          도보 8분       031-708-7040   

                                            요일별_영업시간  \
0  {'목': '08:00 ~ 20:30', '금': '08:00 ~ 20:30', '...   
1  {'목': '07:00 ~ 22:00', '금': '07:00 ~ 22:00', '...   
2  {'목': '08:00 ~ 23:00', '금': '08:00 ~ 23:00', '...   
3  {'월': '11:30 ~ 22:00', '화': '11:30 ~ 22:00', '...   
4  {'월': '12:00 ~ 21:50', '화': '12:00 ~ 21:50', '...   

                                                  리뷰  \
0  {'리뷰 1': {'별점': 4, '리뷰 내용': '원두블렌딩을 원가절감한게 너무 ...   
1  {'리뷰 1': {'별점': 5, '리뷰 내용': '넘 친절한 직원분들! 점심에는 ...   
2  {'리뷰 1': {'별점': 1, '리뷰 내용': '콜라보 굿즈 판매 안하는 매장입...   
3  {'리뷰 1': {'별점': 5, '리뷰 내용': '당근케익 추천받아가지고 포장해서...   
4  {'리뷰 1': {'별점': 3, '리뷰 내용': '리뷰 없음', '날짜': '20...   

                                      url  평균별점  
0    https://place.map.kakao.com/18214074  4.20  
1    https://place.map.kakao.com/27076123  4.24  
2  https://place.map.kakao.com/1165457187  2.94  
3    https://place.map.kakao.com/21657018  3.65  
4   https://place.map.kakao.com/882531039  4.13

### 리뷰 텍스트 전처리 후 SBERT 기반 임베딩

In [13]:
# 모델 로드
model = SentenceTransformer('snunlp/KR-SBERT-V40K-klueNLI-augSTS')

# 불용어 리스트
stopwords = set(['것', '정말', '좀', '너무', '매우', '입니다', '하는', '하고'])

# 단어 반복 줄이기
def reduce_repeated_words(text):
    return re.sub(r'(\b\w+)\1{1,}', r'\1', text)

# 한국어 텍스트 클린 함수
def clean_korean_text(text):
    if not text:
        return ''
    text = emoji.replace_emoji(text, replace='')
    text = re.sub(r'[^가-힣\s]', '', text)
    text = reduce_repeated_words(text)
    words = text.split()
    words = [word for word in words if word not in stopwords]
    return ' '.join(words)

# 리뷰 평균 임베딩 함수
def embed_reviews_avg(review_dict):
    try:
        review_texts = []
        for review_info in review_dict.values():
            content = review_info.get('리뷰 내용', '')
            if content and content != '리뷰 없음':
                cleaned_content = clean_korean_text(content.strip())  # 여기 추가
                if cleaned_content:  # 전처리 후에도 내용이 남아있을 때만
                    print(cleaned_content)
                    review_texts.append(cleaned_content)

        if not review_texts:
            return None

        embeddings = []
        for text in review_texts:
            prompt = f"이 리뷰가 묘사하는 분위기를 임베딩하세요: {text}"
            emb = model.encode(prompt)
            embeddings.append(emb)

        avg_embedding = np.mean(embeddings, axis=0)
        return avg_embedding.tolist() # 리스트로 변환해서 저장
    except Exception as e:
        return None

# 적용
df_reviews['리뷰_평균임베딩'] = df_reviews['리뷰'].apply(embed_reviews_avg)

원두블렌딩을 원가절감한게 과함 종전 리뷰 후 다시 갔는데 프차긴 해도 가격공간이 좋은편도 아니고 맛 하나 보고 가는 곳인데 더보기
분위기 맛 친절 어느 하나 빼놓을 수 없는 맛집 사람들로 항상 북적이는 곳
테크원점보다 여기가 더 맛있게 느껴짐 라떼 맛있음 근처 갈 일 있으면 종 들리는 곳 아이스크림 올라간 라떼도 꽤 별미
라노체 우유거품 아인슈페너 달 카오라떼 코 더보기
비싼데 맛은 그냥 평범한 거 같네요
판교역 알레그리아는 맛없음 좁고 멀어도 무조건 여기로 옴
커피 맛있어요
커알못인데 드립커피 과일향과 맛이 좋음
처음에 매장 들어서자마자 원두 향이 아주 좋다 메리제인은 처음에 밀려오는 산뜻한 과일 향미와 끝에 남는 진한 다크초콜릿 맛이 인상적인 아메리카노다 맛있었 더보기
산미 있는 커피중에 이렇게 향이 좋고 맛있는 커피는 처음 맛봄
맛있어요 워낙 유명합니다
카페 차로 와서 저는 밀크티 마셨어요 달지는 않은데 맛이 부 더보기
메리제인 원두에선 산미있는 다크초콜릿 맛이 났다 다음엔 드립커피로
따뜻한 라떼는 맛있었는데 플랫화이트 아이스는 얼음이 반 평일에는 더 맛있었다는데 편차가 큰가봐요
개인적으로 이렇게 맛이 좋게 산미있는 원두를 찾기 힘들다 생각한다 이제 곧 지방으로 이직하여 내려가는데 이집의 커피가 그리워 본가 올때 자주 와야겠다는 생각을 하게 되는 곳
주말에 방문했고 메리제인 아이스아메리카노 먹었습니다 평이좋아서 간건데 커피 맛있는지 잘모르겠구요 너무시고 씀 친절하다는 느낌도 딱히 내부공간 없음 단 근처회사재직시 프차분위기 질리면 이용할듯합니다
핸드드립전문점 이어서 드립으로 먹었어요 종류도 다양하고 주변에 나무가 많아 통유리로 보이는 풍경이 예뻤습니다 주말 결혼식끝나고 방문이었는데 주차도 여유롭고 좋았습니다
괜찮긴한데 평이 높은 느낌
판교커피맛집 메리제인에 꽂혀서 한 때 거의 매일 가고 겨울엔 원두 사서 핸드드립했었는데 언 더보기
옛날 커피 맛이 안나서 요즘 가끔 가는데 요 메뉴는 맛있었음 내려주는 사람 따라 커피 맛 편차 있음
플랫화이트 마셧는데 짠맛이 

#### 위 코드로 파싱이 안되는 경우 아래 코드 진행(주석 해제 필요)

In [ ]:
# 모델 로드
# model = SentenceTransformer('snunlp/KR-SBERT-V40K-klueNLI-augSTS')

# 불용어 리스트
# stopwords = set(['것', '정말', '좀', '너무', '매우', '입니다', '하는', '하고'])

# 단어 반복 줄이기
# def reduce_repeated_words(text):
#     return re.sub(r'(\b\w+)\1{1,}', r'\1', text)

# 한국어 텍스트 클린 함수
# def clean_korean_text(text):
#     if not text:
#         return ''
#     text = emoji.replace_emoji(text, replace='')
#     text = re.sub(r'[^가-힣\s]', '', text)
#     text = reduce_repeated_words(text)
#     words = text.split()
#     words = [word for word in words if word not in stopwords]
#     return ' '.join(words)

# # 리뷰 평균 임베딩 함수
# def embed_reviews_avg(review_str):
#     try:
#         review_dict = ast.literal_eval(review_str)
#     except:
#         return None

#     review_texts = []
#     for review_info in review_dict.values():
#         content = review_info.get('리뷰 내용', '')
#         if content and content != '리뷰 없음':
#             cleaned_content = clean_korean_text(content.strip())  # 여기 추가
#             if cleaned_content:  # 전처리 후에도 내용이 남아있을 때만
#                 print(cleaned_content)
#                 review_texts.append(cleaned_content)

#     if not review_texts:
#         return None

#     embeddings = []
#     for text in review_texts:
#         prompt = f"이 리뷰가 묘사하는 분위기를 임베딩하세요: {text}"
#         emb = model.encode(prompt)
#         embeddings.append(emb)

#     avg_embedding = np.mean(embeddings, axis=0)
#     return avg_embedding.tolist()  # 리스트로 변환해서 저장

# 적용
# df_reviews['리뷰_평균임베딩'] = df_reviews['리뷰'].apply(embed_reviews_avg)

In [28]:
df_reviews.head()

리뷰  \
0  {'리뷰 1': {'별점': 4, '리뷰 내용': '분위기 맛 친절 어느 하나 빼놓...   
1  {'리뷰 1': {'별점': 5, '리뷰 내용': '2층까지 있지만, 손님이 많아서...   
2  {'리뷰 1': {'별점': 1, '리뷰 내용': '콜라보 굿즈 판매 안하는 매장입...   
3  {'리뷰 1': {'별점': 5, '리뷰 내용': '당근케익 추천받아가지고 포장해서...   
4  {'리뷰 1': {'별점': 3, '리뷰 내용': '한낮인데 문열어둬서 덥고
커피 ...   

                                      url  평균별점  \
0    https://place.map.kakao.com/18214074  4.20   
1    https://place.map.kakao.com/27076123  4.22   
2  https://place.map.kakao.com/1165457187  2.94   
3    https://place.map.kakao.com/21657018  3.65   
4   https://place.map.kakao.com/882531039  4.15   

                                            리뷰_평균임베딩  
0  [-0.9953491687774658, -0.25415077805519104, -0...  
1  [-1.2869690656661987, -0.20615342259407043, -0...  
2  [-0.8153920769691467, -0.29352694749832153, -0...  
3  [-1.0182065963745117, -0.15480491518974304, -0...  
4  [-1.1420519351959229, -0.14602209627628326, -0...

### URL 기반으로 Chroma DB 임베딩 벡터, 평균별점 업데이트

#### Chroma DB 업데이트 이전 데이터 형식 검사

In [14]:
for idx, row in df_reviews.iterrows():
    url = row['url']
    embedded_vector = row['리뷰_평균임베딩']
    avg_score = row['평균별점']

    # 데이터 형식 검사
    if not isinstance(url, str):
        print(f"[url 오류] idx {idx}: {url}")
        continue

    if not (isinstance(embedded_vector, list) and all(isinstance(x, (int, float)) for x in embedded_vector)):
        print(f"[임베딩 오류] idx {idx}: {type(embedded_vector)} / 값 일부: {str(embedded_vector)[:100]}")
        continue

    if not isinstance(avg_score, (int, float)):
        print(f"[평균별점 오류] idx {idx}: {avg_score}")
        continue

[임베딩 오류] idx 40: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 49: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 60: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 64: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 80: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 83: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 92: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 94: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 118: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 124: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 175: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 199: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 202: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 234: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 245: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 263: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 310: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 316: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 372: <class 'NoneType'> / 값 일부: None
[임베딩 오류] idx 440: <class 'NoneType'> / 값 일부: None
[임베딩 오류]

In [15]:
df_missing_embed = df_reviews[df_reviews['리뷰_평균임베딩'].isnull()]
print(f"❗ 임베딩이 누락된 행 수: {len(df_missing_embed)}")
print(df_missing_embed[['url', '리뷰', '평균별점', '리뷰_평균임베딩']].head())

❗ 임베딩이 누락된 행 수: 59
                                       url  리뷰  평균별점 리뷰_평균임베딩
40    https://place.map.kakao.com/10537599  {}   NaN     None
49    https://place.map.kakao.com/14577391  {}   NaN     None
60  https://place.map.kakao.com/2071896518  {}   NaN     None
64  https://place.map.kakao.com/1910973245  {}   NaN     None
80  https://place.map.kakao.com/2029056166  {}   NaN     None


#### 임베딩 누락 건(리뷰, 평균별점이 있음에도 리뷰_평균임베딩, 평균별점 컬럼이 누락인 경우) 재시도

In [16]:
# 나중에 재처리할 row 저장
failed_rows = []

for idx, row in df_reviews.iterrows():
    url = row['url']
    embedded_vector = row['리뷰_평균임베딩']
    avg_score = row['평균별점']

    if not (isinstance(embedded_vector, list) and all(isinstance(x, (int, float)) for x in embedded_vector)):
        failed_rows.append(idx)
        continue

In [17]:
model = SentenceTransformer("snunlp/KR-SBERT-V40K-klueNLI-augSTS")

for idx in failed_rows:
    text = df_reviews.loc[idx, '리뷰']
    if isinstance(text, str) and "리뷰 없음" not in text:
        embedding = model.encode(text).tolist()
        df_reviews.at[idx, '리뷰_평균임베딩'] = embedding

#### 재확인 (재확인 이후에도 별도 오류가 없는 경우 업데이트 및 삭제 진행)

In [18]:
df_missing_embed = df_reviews[df_reviews['리뷰_평균임베딩'].isnull()]
print(f"❗ 임베딩이 누락된 행 수: {len(df_missing_embed)}")
print(df_missing_embed[['url', '리뷰', '평균별점']].head())

❗ 임베딩이 누락된 행 수: 59
                                       url  리뷰  평균별점
40    https://place.map.kakao.com/10537599  {}   NaN
49    https://place.map.kakao.com/14577391  {}   NaN
60  https://place.map.kakao.com/2071896518  {}   NaN
64  https://place.map.kakao.com/1910973245  {}   NaN
80  https://place.map.kakao.com/2029056166  {}   NaN


### DB Update

In [34]:
THRESHOLD = 90

not_found = []
updated_url = set()
updated_count = 0

for idx, row in df_reviews.iterrows():
    url = row['url'].strip()
    embedded_vector = row['리뷰_평균임베딩']
    avg_score = row['평균별점']

    # 결측 처리 플래그
    is_valid_embedding = isinstance(embedded_vector, list) and all(isinstance(x, (int, float)) for x in embedded_vector)
    is_valid_score = isinstance(avg_score, (int, float)) and not math.isnan(avg_score)

    if not is_valid_embedding and not is_valid_score:
        print(f"[스킵] 둘 다 없음 → idx {idx}, url: {url}")
        continue

    try:
        results = review_collection.get(
            where={"링크": url}
        )
        print(f"검색 결과 → idx {idx + 1}, url: {url}, results: {results}")

        if results["ids"]:
            doc_id = results["ids"][0]
            metadata = results["metadatas"][0]
            print(f"문서 찾음 → idx {idx + 1}, url: {url}, doc_id: {doc_id}")
            
            place_name_db = metadata.get("상호명", "").strip()
            place_name_df = row['상호명'].strip()
            print(f"DB 상호명: {place_name_db}, DF 상호명: {place_name_df}")

            sim = fuzz.ratio(place_name_db, place_name_df)
            print(f"유사도: {sim} ({place_name_db} vs {place_name_df})")
            
            if sim < THRESHOLD:
                print(f"상호명 유사도 낮음 ({sim}) → idx {idx}, DB: {place_name_db}, DF: {place_name_df}")
                continue

            update_kwargs = {"ids": [doc_id]}

            if is_valid_embedding:
                update_kwargs["embeddings"] = embedded_vector
            if is_valid_score:
                update_kwargs["metadatas"] = [{"평균별점": avg_score}]

            review_collection.update(**update_kwargs)
            updated_url.add(url)
            updated_count += 1
            print(f"Updated {url}")
    except:
        print(f"문서 찾을 수 없음 → idx {idx + 1}, url: {url}")
        not_found.append({"idx": idx + 1, "url": url})
        
print(f"업데이트 문서 수: {updated_count}")           

검색 결과 → idx 1, url: https://place.map.kakao.com/18214074, results: {'ids': ['review_collection__review_collection__store_0'], 'embeddings': None, 'documents': ['알레그리아 판교테크노밸리점'], 'uris': None, 'included': ['metadatas', 'documents'], 'data': None, 'metadatas': [{'영업시간': '월, 목, 토, 일: 10:00~20:30, 화, 수, 금: 08:00~20:30', '위도': 37.4012850380545, '상호명': '알레그리아 판교테크노밸리점', '링크': 'https://place.map.kakao.com/18214074', '주소': '경기 성남시 분당구 판교역로 230 삼환하이펙스 B동 1층 119호', '경도': 127.11045570879, '대표카테고리': '카페/디저트', '평균별점': 4.2}]}
문서 찾음 → idx 1, url: https://place.map.kakao.com/18214074, doc_id: review_collection__review_collection__store_0
DB 상호명: 알레그리아 판교테크노밸리점, DF 상호명: 알레그리아 판교테크노밸리점
유사도: 100 (알레그리아 판교테크노밸리점 vs 알레그리아 판교테크노밸리점)
Updated https://place.map.kakao.com/18214074
검색 결과 → idx 2, url: https://place.map.kakao.com/27076123, results: {'ids': ['review_collection__review_collection__store_1'], 'embeddings': None, 'documents': ['스타벅스 판교역로점'], 'uris': None, 'included': ['metadatas', 'documents'], 'dat

### Update가 일어나지 않은 데이터는 품질이 저하된 데이터로 간주, 삭제 처리

In [37]:
# 크로마DB에서 전체 문서의 id, 메타데이터 불러오기
all_docs = review_collection.get(include=['metadatas'])

# 크로마DB에 있는 url 목록
chromadb_urls = [meta.get('링크', '').strip() for meta in all_docs['metadatas']]
# 삭제해야 할 url = chroma에는 있는데, updated_url에는 없는 것
urls_to_delete = set(chromadb_urls) - updated_url
print("삭제할 url:", urls_to_delete)
print(len(urls_to_delete), "개 url 삭제 예정")

삭제할 url: {'https://place.map.kakao.com/26314261', 'https://place.map.kakao.com/1837479176', 'https://place.map.kakao.com/27445997', 'https://place.map.kakao.com/11607082', 'https://place.map.kakao.com/24324934', 'https://place.map.kakao.com/1174471186', 'https://place.map.kakao.com/958651617', 'https://place.map.kakao.com/590679717', 'https://place.map.kakao.com/1683395936', 'https://place.map.kakao.com/14601427', 'https://place.map.kakao.com/1257664984', 'https://place.map.kakao.com/454243463', 'https://place.map.kakao.com/119437302', 'https://place.map.kakao.com/1527538187', 'https://place.map.kakao.com/15951582', 'https://place.map.kakao.com/1607284381', 'https://place.map.kakao.com/1705971541', 'https://place.map.kakao.com/10537599', 'https://place.map.kakao.com/576726241', 'https://place.map.kakao.com/99513625', 'https://place.map.kakao.com/1853910181', 'https://place.map.kakao.com/620553532', 'https://place.map.kakao.com/348787835', 'https://place.map.kakao.com/1247179094', 'http

In [38]:
delete_count = 0

for meta, doc_id in zip(all_docs['metadatas'], all_docs['ids']):
    url = meta.get('링크', '').strip()
    if url in urls_to_delete:
        # doc_id가 리스트로 반환될 때도 있으니
        del_id = doc_id if isinstance(doc_id, str) else doc_id[0]
        review_exists = review_collection.get(ids=[del_id])['ids'] != []
        menu_exists = menu_collection.get(where={"링크": url})['ids'] != []
        
        if review_exists and menu_exists:
            try:
                review_collection.delete(ids=[del_id])
                menu_collection.delete(where={"링크": url})
                delete_count += 1
                print(f"삭제 완료: url={url}, id={del_id}")
            except Exception as e:
                print(f"[삭제 실패] url={url}, error: {e}")
        else:
            print(f"둘 다 있는 경우에만 삭제! (review: {review_exists}, menu: {menu_exists})")
            
print(f"총 삭제된 문서 수: {delete_count}")

삭제 완료: url=https://place.map.kakao.com/10537599, id=review_collection__review_collection__store_41
삭제 완료: url=https://place.map.kakao.com/14577391, id=review_collection__review_collection__store_52
삭제 완료: url=https://place.map.kakao.com/2071896518, id=review_collection__review_collection__store_64
삭제 완료: url=https://place.map.kakao.com/1910973245, id=review_collection__review_collection__store_69
삭제 완료: url=https://place.map.kakao.com/2029056166, id=review_collection__review_collection__store_87
삭제 완료: url=https://place.map.kakao.com/26924590, id=review_collection__review_collection__store_90
삭제 완료: url=https://place.map.kakao.com/1290027367, id=review_collection__review_collection__store_99
삭제 완료: url=https://place.map.kakao.com/454243463, id=review_collection__review_collection__store_101
삭제 완료: url=https://place.map.kakao.com/1060969044, id=review_collection__review_collection__store_130
삭제 완료: url=https://place.map.kakao.com/2134470293, id=review_collection__review_collection__stor

### DB 데이터 재확인(타 데이터 유실 여부 확인)

In [40]:
# 1) 카운트 확인 (전체 문서 수)
print("리뷰 개수:", review_collection.count())
print("메뉴 개수:", menu_collection.count())

리뷰 개수: 1176
메뉴 개수: 1176


In [6]:
collection_list = [c.name for c in chroma_client.list_collections()]
print("크로마DB에 있는 컬렉션:", collection_list)

크로마DB에 있는 컬렉션: ['hobby_subtraits', 'mbti_traits', 'user_history', 'mbti_feeds', 'review_collection', 'hated_mission_collection', 'mission_collection', 'user_latest', 'recommendation_history', 'menu_collection']


In [8]:
for my_collection in collection_list:
    collection = chroma_client.get_collection(name=my_collection)
    print(f"{my_collection} 컬렉션 문서 수:", collection.count())
    print(f"{my_collection} 컬렉션 메타데이터 샘플:", collection.get(include=["metadatas"])["metadatas"][:5])
    print()

hobby_subtraits 컬렉션 문서 수: 6000
hobby_subtraits 컬렉션 메타데이터 샘플: [{'Subtrait': '드리블', 'Weight': 0.9, 'Hobby': '축구(하기)'}, {'Weight': 0.8, 'Hobby': '축구(하기)', 'Subtrait': '슈팅'}, {'Subtrait': '패싱', 'Weight': 0.7, 'Hobby': '축구(하기)'}, {'Hobby': '축구(하기)', 'Subtrait': '헤딩', 'Weight': 0.6}, {'Weight': 0.5, 'Hobby': '축구(하기)', 'Subtrait': '수비'}]

mbti_traits 컬렉션 문서 수: 6528
mbti_traits 컬렉션 메타데이터 샘플: [{'MBTI': 'ENTP', 'Weight': 1.0, 'Trait': '창의적'}, {'Weight': 0.95, 'Trait': '호기심 많은', 'MBTI': 'ENTP'}, {'MBTI': 'ENTP', 'Trait': '논리적', 'Weight': 0.93}, {'MBTI': 'ENTP', 'Trait': '재치 있는', 'Weight': 0.92}, {'Weight': 0.9, 'Trait': '자유로운', 'MBTI': 'ENTP'}]

user_history 컬렉션 문서 수: 5
user_history 컬렉션 메타데이터 샘플: [{'tf_score': 50, 'jp_score': 50, 'user_id': 1, 'ei_score': 50, 'sn_score': 50, 'hobby_name': '코딩', 'timestamp': '2025-05-15T14:09:55.484399'}, {'tf_score': 70, 'sn_score': 40, 'hobby_name': '등산', 'ei_score': 60, 'user_id': 2, 'timestamp': '2025-05-15T14:10:11.847667', 'jp_score': 30}, {'jp_score': 50, '